In [1]:
using Pkg
Pkg.activate(".")
using PlotlyJS, Zygote, LinearAlgebra

function frenet_frame(x,y,z)
    ẋ(t)= gradient(x,t)[1]
    ẏ(t)= gradient(y,t)[1]
    ż(t)= gradient(z,t)[1]

    ẍ(t)= hessian(x,t)
    ÿ(t)= hessian(y,t)
    z̈(t)= hessian(z,t)

    α̇(t) = [ẋ(t),ẏ(t),ż(t)]
    α̈(t) = [ẍ(t),ÿ(t),z̈(t)]
    function out(t)
        T = α̇(t)
        T = T/norm(T)
        ad = α̈(t)
        N = ad-dot(ad,T)T
        N = N/norm(N)
        B = cross(T,N)
        T,N,B
    end
end

function uv_surface(uv_domain,ϕ; uv_res = [40,40])
    us = LinRange(uv_domain[1],uv_domain[2],uv_res[1])
    vs = LinRange(uv_domain[3],uv_domain[4],uv_res[2])
    u_res, v_res = uv_res
    xs = zeros(u_res,v_res)
    ys = zeros(u_res,v_res)
    zs = zeros(u_res,v_res)
    for (i,u) in enumerate(us)
        for (j,v) in enumerate(vs)
            xs[i,j], ys[i,j],zs[i,j] = ϕ(u,v)
        end
    end
    surface(x=xs,y=ys,z=zs)
end

function xyz(ps)
    x = [p[1] for p in ps]
    y = [p[2] for p in ps]
    z = [p[3] for p in ps]
    return x,y,z
end

function toric_knot(m::Int64, n::Int64; R=2, r=1, uv_res = [100,100])
    ϕ(u,v) = [(R+r*cos(u))*cos(v),(R+r*cos(u))*sin(v),r*sin(u)]
    α(t) = ϕ(m*t,n*t)
    x(t) = α(t)[1]
    y(t) = α(t)[2]
    z(t) = α(t)[3]

    F = frenet_frame(x,y,z);
    function ψ(u,v)
        T,N,B = F(u)
        ρ=r/3
        α(u) + ρ*cos(v)*N + ρ*sin(v)*B
    end
    uv_surface([-π,π,-π,π],ψ,uv_res=uv_res)
end

WebIO._IJuliaInit()

  Activating environment at `~/Dropbox/Upwork/Plotly/DashKnots.jl/Project.toml`


toric_knot (generic function with 1 method)

In [2]:
plot(toric_knot(2,2,uv_res=[200,200]))

data: [
  "surface with fields type, x, y, and z"
]

layout: "layout with fields margin and template"